# Saudi Arabia Weather EDA:
_Auther: Esraa Madi_


-------

Dataset: [Saudi Arabia Weather History](https://www.kaggle.com/esraamadi/saudi-arabia-weather-history)

_Note: some d-tale tables and plotly plots aren't rendered on github, in case plots are not shown, you can check this notebook on_ [nbviewer](https://nbviewer.jupyter.org/github/EsraaMadi/KSA-weather-forecasting/blob/master/weather_EDA.ipynb)

In [2]:
# import libs
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
import dtale
import plotly.express as px
import datetime
import pickle

In [66]:
# Read data
df = pd.read_csv("datasets/weather-sa-2017-2019-clean.csv", index_col=0)
df.head()

city            date   time  year  month  day  hour  minute weather  \
0  Qassim  1 January 2017  00:00  2017      1    1    24       0  Clear    
1  Qassim  1 January 2017  01:00  2017      1    1     1       0  Clear    
2  Qassim  1 January 2017  03:00  2017      1    1     3       0  Clear    
3  Qassim  1 January 2017  04:00  2017      1    1     4       0  Clear    
4  Qassim  1 January 2017  05:00  2017      1    1     5       0  Clear    

   temp  wind humidity  barometer  visibility  
0    17    11      64%     1018.0          16  
1    17     6      64%     1018.0          16  
2    15    11      72%     1019.0          16  
3    15    11      72%     1019.0          16  
4    15     9      72%     1019.0          16

In [67]:
# check data size
df.shape

(249023, 14)

In [68]:
# check missing values
df.isnull().sum()

city           0
date           0
time           0
year           0
month          0
day            0
hour           0
minute         0
weather        0
temp           0
wind           0
humidity      17
barometer     72
visibility     0
dtype: int64

In [69]:
# check types
df.dtypes

city           object
date           object
time           object
year            int64
month           int64
day             int64
hour            int64
minute          int64
weather        object
temp            int64
wind            int64
humidity       object
barometer     float64
visibility      int64
dtype: object

In [70]:
# fix humidity col type
df['humidity'] = df.humidity.map(lambda x: float(str(x).replace('%', '')))

In [71]:
# fix date column
df.date = pd.to_datetime(df['date']) 

In [72]:
# work on date col 

In [73]:
df.date.describe()

count                  249023
unique                    850
top       2018-11-24 00:00:00
freq                      321
first     2017-01-01 00:00:00
last      2019-04-30 00:00:00
Name: date, dtype: object

In [74]:
start_date = df.date.min()
start_date

Timestamp('2017-01-01 00:00:00')

In [75]:
end_date = df.date.max()
end_date

Timestamp('2019-04-30 00:00:00')

In [76]:
# set date as index
df.set_index('date', inplace=True)
#df.sort_index(inplace=True) # will not do since we have same day for each city (we will sort dates for each city later)

In [77]:
df.head()

city   time  year  month  day  hour  minute weather  temp  wind  \
date                                                                            
2017-01-01  Qassim  00:00  2017      1    1    24       0  Clear     17    11   
2017-01-01  Qassim  01:00  2017      1    1     1       0  Clear     17     6   
2017-01-01  Qassim  03:00  2017      1    1     3       0  Clear     15    11   
2017-01-01  Qassim  04:00  2017      1    1     4       0  Clear     15    11   
2017-01-01  Qassim  05:00  2017      1    1     5       0  Clear     15     9   

            humidity  barometer  visibility  
date                                         
2017-01-01      64.0     1018.0          16  
2017-01-01      64.0     1018.0          16  
2017-01-01      72.0     1019.0          16  
2017-01-01      72.0     1019.0          16  
2017-01-01      72.0     1019.0          16

In [78]:
# check correlations between columns
df.corr()

year     month       day      hour    minute      temp  \
year        1.000000 -0.311509 -0.010175 -0.002183 -0.000084 -0.184575   
month      -0.311509  1.000000  0.012757 -0.001278 -0.004283  0.225099   
day        -0.010175  0.012757  1.000000  0.000806 -0.000638  0.021591   
hour       -0.002183 -0.001278  0.000806  1.000000  0.009323  0.211126   
minute     -0.000084 -0.004283 -0.000638  0.009323  1.000000 -0.007888   
temp       -0.184575  0.225099  0.021591  0.211126 -0.007888  1.000000   
wind        0.045206 -0.100243  0.017328  0.202639  0.069682  0.238350   
humidity    0.155729 -0.043035 -0.012102 -0.147634  0.025058 -0.596427   
barometer   0.088847 -0.052225 -0.002519 -0.025088 -0.015394 -0.681920   
visibility -0.064775  0.020941 -0.024035 -0.080893 -0.068198 -0.001876   

                wind  humidity  barometer  visibility  
year        0.045206  0.155729   0.088847   -0.064775  
month      -0.100243 -0.043035  -0.052225    0.020941  
day         0.017328 -0.012102  -0.002519   -0.024035  
hour        0.202639 -0.147634  -0.025088   -0.080893  
minute      0.069682  0.025058  -0.015394   -0.068198  
temp        0.238350 -0.596427  -0.681920   -0.001876  
wind        1.000000 -0.179045  -0.134896   -0.210594  
humidity   -0.179045  1.000000   0.290881   -0.151316  
barometer  -0.134896  0.290881   1.000000   -0.033042  
visibility -0.210594 -0.151316  -0.033042    1.000000

In [79]:
# above shows strong relation between temp and each humidity and barometer
df.corr()['temp'][['humidity', 'barometer']]

humidity    -0.596427
barometer   -0.681920
Name: temp, dtype: float64

In [80]:
# and kind of relation between visibility and wind
df.corr()['wind']['visibility']

-0.21059419970952814

In [81]:
# let's check these corellations using plot below

In [82]:
# Assigning a reference to a running D-Tale process

d = dtale.show(df, index_col=0, notebook=True)


In [83]:
### using above link you can do the following: (http://localhost:40000/dtale/main/1)
# 1. change cols types
# 2. detect outliers
# 3. get describe info
# 4. check cols correlation
# 5. value counts for categorical cols
# 6. replace col values (fill missing data)
# 7. Interactive Column Filtering
# 8. direct edit cells values 
# 9. drow charts

### you can learn about using feaures above from:
###   i. short videos https://www.youtube.com/channel/UCJiHoGUG0hsbEGPv-MyuWMA
###   ii. https://pypi.org/project/dtale/

In [20]:
# relation between visibility and wind
d.offline_chart(chart_type='line', x='date', y=['wind', 'visibility'], agg='mean');

In [21]:
# as we can see we have a negative relationship between visibility and wind
# when wind increases , visibility decrease and vice versa

In [22]:
# relation between temp and each humidity and barometer
d.offline_chart(chart_type='line', x='date', y=['temp', 'barometer', 'humidity'], agg='mean');

In [23]:
# we need to scale them to check correlation in the plot

In [84]:
# define min max scaler
scaler = MinMaxScaler()
# transform data
df_scaled_arr = scaler.fit_transform(df[['temp', 'barometer', 'humidity']])

In [85]:
df_scaled = pd.DataFrame(df_scaled_arr, columns=['temp', 'barometer', 'humidity'])

In [86]:
df_scaled['date'] = df.index
df_scaled.set_index('date', inplace=True)

In [87]:
df_scaled.head()

temp  barometer  humidity
date                                     
2017-01-01  0.388889   0.578680      0.64
2017-01-01  0.388889   0.578680      0.64
2017-01-01  0.351852   0.583756      0.72
2017-01-01  0.351852   0.583756      0.72
2017-01-01  0.351852   0.583756      0.72

In [88]:
d_scaled = dtale.show(df_scaled, index_col=0, notebook=True)

In [29]:
d_scaled.offline_chart(chart_type='line', x='date', y=['temp', 'barometer', 'humidity'], agg='mean');

In [30]:
# as we can see we have negative relationship between temp and other columns (barometer, humidity)
# when temperature increase, both barometer, humidity decrese and vice versa

In [31]:
# some other intersting plots 
# temperature plot 
d.offline_chart(chart_type='line', x='date', y='temp', agg='mean', group='year');

In [ ]:
# we have temp from Jan 2017 to almost Apr 2019 (2 years and 4 months)
# seems seasonal time series

In [ ]:
# from this site, there are four Seasons in Saudi Arabia :

#  December - January - February: Winter
#  March - April: Spring 
#  May - June - July - August - Septemper: Summer
#  October - November: Autom

# we can see that these seasons match our data

In [32]:
# Wind plot
d.offline_chart(chart_type='line', x='date', y='wind', agg='mean', group='year');

In [ ]:
# seems seasonal time series
# Over 3 years, we notice these is wind blow on KSA (increase) from Jan to Apr
# over 2 years , we notice there is wind does not blow that much (decrese) from Jul to Oct

In [194]:
# lets check it for each city (click on the city you want on the plot to show its vis)
d.offline_chart(chart_type='line', x='date', y='wind', agg='mean', group='city');

In [195]:
# Humidity
d.offline_chart(chart_type='line', x='date', y='humidity', agg='mean', group='year');

In [ ]:
# it seems there is some kind of a humidity behaviour related to months of year

In [226]:
# let's check for each city Individually and corresponding temp 
# 1. for Riyadh, Hail, Madina, Qassim, Northern boarder, Jawf, tabuk cities 
d.offline_chart(chart_type='line', x='date', y='humidity', agg='mean', group='city');
d.offline_chart(chart_type='line', x='date', y='temp', agg='mean', group='city');

In [ ]:
# as we can see these cities (middel and north cities) hava same behaviour of humidity according to months
# - humidity decreses in summer-hot (high temp) months and increase in cold months (winter)

In [227]:
# 2- najran and jazan
d.offline_chart(chart_type='line', x='date', y='humidity', agg='mean', group='city');
d.offline_chart(chart_type='line', x='date', y='temp', agg='mean', group='city');

In [ ]:
# najran and jazan show almost the same trend in Humility since they have similar temp

In [22]:
# Barometer
d.offline_chart(chart_type='line', x='date', y='barometer', agg='mean', group='year');

In [ ]:
# seems seasonal time series

In [33]:
# # let's check for each city Individually and corresponding temp 
d.offline_chart(chart_type='line', x='date', y='barometer', agg='mean', group='city');
d.offline_chart(chart_type='line', x='date', y='temp', agg='mean', group='city');

In [ ]:
# it clearly shows that there is a negative relation between city's temp and city's barometer 

In [34]:
# Visibility 
d.offline_chart(chart_type='line', x='date', y='visibility', agg='mean', group='year');

In [ ]:
# seems noisy series (not related to months)

In [89]:
# check how avg temp for each month in the year changes over years 
# is winter getting more cold or summer getting more hotter?
d.offline_chart(chart_type='scatter', x='city', y='temp', agg='mean', group='year');

In [ ]:
# 2019 is lower temp since we just have data for first 4 months + we cant see months so let's try different graph 

In [17]:
# lets get avg weather info for each city 
df.groupby(['city', 'month',  'year']).mean()[['temp', 'wind', 'humidity', 'barometer', 'visibility']]

temp       wind   humidity    barometer  visibility
city  month year                                                          
Assir 1     2017  16.421271   9.465470  58.957182  1024.988950   13.453039
            2019  17.125512  10.922237  51.613915  1025.362892   14.185539
      2     2017  16.104615  15.104615  66.149231  1023.480000    7.600000
            2019  17.484018  15.611872  58.039574  1024.021309    9.797565
      3     2017  19.056708  16.886584  54.450899  1022.529737    9.567082
...                     ...        ...        ...          ...         ...
Tabuk 10    2018  25.326613  12.767473  31.458333  1015.793011    8.369624
      11    2017  18.050350   8.441958  40.110490  1016.668067   10.009790
            2018  17.760779  10.090403  49.553547  1016.378303    3.265647
      12    2017  14.525745   8.979675  37.146341  1020.322931   12.967480
            2018  13.413555   9.706777  47.991701  1018.260028    9.421853

[351 rows x 5 columns]

In [60]:
# weather info for each month
df_months = list(df.groupby('month'))

In [26]:
# plot temp changes over years for each city

In [64]:
for month_num, df_month in df_months:
    df_temp = df_month.groupby(['city', 'year'], as_index=False)[['temp']].mean()
    df_temp['year'] = df_temp.year.astype('object')
    month_name = datetime.date(2020, month_num, 1).strftime('%B')
    fig = px.scatter(df_temp, x="city", y="temp",
                     color="year", size='temp',
                     title=f'Average Temperature for each City in {month_name} from 2017-2019')
    fig.show()

In [ ]:
# from above charts we can notice:
#  Winter season start late (almost feb) in 2019 than other years 
#  2017 was hotter year than 2018 in general

In [90]:
# from charts above we can see there are missing dates between recoreds
pd.date_range(start = start_date, end = end_date).difference(df.index)

DatetimeIndex([], dtype='datetime64[ns]', freq=None)

In [91]:
# overall we don't have any missing dates in the middel

In [92]:
# let's check each city individually

In [93]:
df['city'].value_counts() # shows diff no of rows which means there are missing dates

Jawf                20352
Mecca               20268
Tabuk               20240
Northern boarder    20235
Hail                20121
Madina              19965
Baha                19959
Najran              19847
Jazan               19829
Qassim              19793
EP                  18505
Riyadh              16421
Assir               13488
Name: city, dtype: int64

In [94]:
# get all cities names
cities = list(df['city'].unique())
cities[:5]

['Qassim', 'Hail', 'Madina', 'EP', 'Riyadh']

In [95]:
# calculate missing days in each city
df_cities_lst = []
for city in cities:
    df_city = df[df['city'] == city]
    df_cities_lst.append(df_city)
    missing_dates = pd.date_range(start = start_date, end = end_date ).difference(df_city.index).shape[0]
    print(f'city: {city}==> has missing days equal {missing_dates}')

city: Qassim==> has missing days equal 13
city: Hail==> has missing days equal 0
city: Madina==> has missing days equal 0
city: EP==> has missing days equal 0
city: Riyadh==> has missing days equal 165
city: Mecca==> has missing days equal 0
city: Tabuk==> has missing days equal 0
city: Assir==> has missing days equal 273
city: Northern boarder==> has missing days equal 0
city: Jazan==> has missing days equal 0
city: Najran==> has missing days equal 0
city: Baha==> has missing days equal 0
city: Jawf==> has missing days equal 0


In [96]:
def resample_data(df, time_freq):
    """ downsample data to given frequency"""
    
    # create the new index and a new series full of NaNs
    new_index = pd.date_range(start=df.index.min(),
                                 end=df.index.max(),
                                 freq=time_freq)

    new_series = pd.Series(np.nan, index=new_index)

    # concat the old and new series and remove duplicates (if any) 
    comb_series = pd.concat([df, new_series])
    comb_series = comb_series.iloc[:, 1:]
    comb_series = comb_series[~comb_series.index.duplicated(keep='first')]
    comb_series.interpolate(method='nearest', inplace=True)
    comb_series.sort_index(inplace=True)
    
    return comb_series

In [97]:
def concat_unnumerical_col(ts_df, not_num_df, col_names):
    """Function to concate Categorical columns to timeseries data that have diff index """
    indices = np.searchsorted(ts_df.index.values, not_num_df.index.values)
    for col_name in col_names:
        not_num_df[col_name] = indices
        not_num_df[col_name] = not_num_df[col_name].map(lambda x: ts_df[col_name].iloc[x])
    return not_num_df

In [98]:
# downsampling our data to be tempreture every 3 hours and fill missing
for ind, df_city in enumerate(df_cities_lst):
    df_temp = resample_data(df_city[['temp', 'wind', 'humidity', 'barometer', 'visibility']], '3H') 
    df_temp = concat_unnumerical_col(df_city, df_temp, ['city', 'weather'])
    df_cities_lst[ind] = df_temp

In [99]:
# check all cities have same number of dates
for df_city, city_name in zip(df_cities_lst, cities):
    missing_dates = pd.date_range(start = df_city.index.min(), end = df_city.index.max()).difference(df_city.index).shape[0]
    print(f'{city_name}==> has missing days equals {missing_dates}')

Qassim==> has missing days equals 0
Hail==> has missing days equals 0
Madina==> has missing days equals 0
EP==> has missing days equals 0
Riyadh==> has missing days equals 0
Mecca==> has missing days equals 0
Tabuk==> has missing days equals 0
Assir==> has missing days equals 0
Northern boarder==> has missing days equals 0
Jazan==> has missing days equals 0
Najran==> has missing days equals 0
Baha==> has missing days equals 0
Jawf==> has missing days equals 0


In [101]:
# save dataset after preprocessing
outfile = open('datasets/clean_cities_dataset','wb')
pickle.dump(df_cities_lst,outfile)
pickle.dump(cities,outfile)
outfile.close()

In [83]:
# create another format of data which is all cities tempruture values Correspond to same dates

# new data frame
df_wide = pd.DataFrame()

for df_, city in zip(df_cities_lst, cities):
    # change columns names as city name
    df_.columns = [f"{col_name}_{city}"for col_name in df_.columns]
    df_wide = pd.merge(df_wide, df_.iloc[:,0:5], how='outer', sort=True, left_index=True, right_index=True)

In [84]:
# check shape of merged datafram
df_wide.shape

(6793, 65)

In [85]:
# show some data
df_wide.head()

barometer_Qassim  humidity_Qassim  temp_Qassim  \
2017-01-01 00:00:00            1018.0             64.0         17.0   
2017-01-01 03:00:00            1018.0             64.0         17.0   
2017-01-01 06:00:00            1018.0             64.0         17.0   
2017-01-01 09:00:00            1018.0             64.0         17.0   
2017-01-01 12:00:00            1018.0             64.0         17.0   

                     visibility_Qassim  wind_Qassim  barometer_Hail  \
2017-01-01 00:00:00               16.0         11.0          1018.0   
2017-01-01 03:00:00               16.0         11.0          1018.0   
2017-01-01 06:00:00               16.0         11.0          1018.0   
2017-01-01 09:00:00               16.0         11.0          1018.0   
2017-01-01 12:00:00               16.0         11.0          1018.0   

                     humidity_Hail  temp_Hail  visibility_Hail  wind_Hail  \
2017-01-01 00:00:00           64.0       17.0             16.0       11.0   
2017-01-01 03:00:00           64.0       17.0             16.0       11.0   
2017-01-01 06:00:00           64.0       17.0             16.0       11.0   
2017-01-01 09:00:00           64.0       17.0             16.0       11.0   
2017-01-01 12:00:00           64.0       17.0             16.0       11.0   

                     ...  barometer_Baha  humidity_Baha  temp_Baha  \
2017-01-01 00:00:00  ...          1023.0           59.0       15.0   
2017-01-01 03:00:00  ...          1023.0           59.0       15.0   
2017-01-01 06:00:00  ...          1023.0           59.0       15.0   
2017-01-01 09:00:00  ...          1023.0           59.0       15.0   
2017-01-01 12:00:00  ...          1023.0           59.0       15.0   

                     visibility_Baha  wind_Baha  barometer_Jawf  \
2017-01-01 00:00:00             16.0        0.0          1022.0   
2017-01-01 03:00:00             16.0        0.0          1022.0   
2017-01-01 06:00:00             16.0        0.0          1022.0   
2017-01-01 09:00:00             16.0        0.0          1022.0   
2017-01-01 12:00:00             16.0        0.0          1022.0   

                     humidity_Jawf  temp_Jawf  visibility_Jawf  wind_Jawf  
2017-01-01 00:00:00           43.0       10.0             16.0        7.0  
2017-01-01 03:00:00           43.0       10.0             16.0        7.0  
2017-01-01 06:00:00           43.0       10.0             16.0        7.0  
2017-01-01 09:00:00           43.0       10.0             16.0        7.0  
2017-01-01 12:00:00           43.0       10.0             16.0        7.0  

[5 rows x 65 columns]

In [87]:
# check null values
df_wide.isnull().sum()

barometer_Qassim     104
humidity_Qassim      104
temp_Qassim          104
visibility_Qassim    104
wind_Qassim          104
                    ... 
barometer_Jawf         0
humidity_Jawf          0
temp_Jawf              0
visibility_Jawf        0
wind_Jawf              0
Length: 65, dtype: int64

In [89]:
# fill missing data
df_wide = df_wide.interpolate(method='time')
df_wide.isnull().sum()

barometer_Qassim     0
humidity_Qassim      0
temp_Qassim          0
visibility_Qassim    0
wind_Qassim          0
                    ..
barometer_Jawf       0
humidity_Jawf        0
temp_Jawf            0
visibility_Jawf      0
wind_Jawf            0
Length: 65, dtype: int64

In [90]:
# save new dataset
outfile = open('datasets/clean_cities_dataset','wb')
pickle.dump(df_wide,outfile)
outfile.close()